In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import warnings
from scipy import stats
from collections import Counter
from scipy.stats import pointbiserialr
from math import sqrt
import copy
import math
from scipy.stats import chi2


def data_get():
    disese = pd.read_csv(r"D:\jupyter\new_funtion\mRNA_LncRNA_Non_Small_Cell_Lung_Carcinoma.csv")
    health = pd.read_csv(r"D:\jupyter\new_funtion\mRNA_LncRNA_Non_Small_Cell_Lung_Carcinoma_HC.csv")
    dat = disese[disese['gene_type'] == "lncRNA"]
    tes = health[health['gene_type'] == "lncRNA"]
    return dat, tes

def data_cut(dat):
    dat_T_test = dat.iloc[:, 6:]
    dat_T_test = dat_T_test.transpose()
    y = dat.iloc[:, 2].values
    dat_T_test.columns = [y]
    return dat_T_test

def T_test(dat,tes):
    res = {}
    for i in range(dat.shape[0]):
        geneName = dat['gene_name'].to_list()[i]
        pvalue = stats.levene(dat.iloc[i, 6:].to_numpy(), tes.iloc[i, 6:].to_numpy(), center='median').pvalue
        if pvalue < 0.05:
            res[geneName] = pvalue
    return  res

def T_test_r():
    dat, tes = data_get()
    res = {}
    for i in range(dat.shape[0]):
        geneName = dat['gene_name'].to_list()[i]
        pvalue = stats.levene(dat.iloc[i, 6:].to_numpy(), tes.iloc[i, 6:].to_numpy(), center='median').pvalue
        if pvalue < 0.05:
            res[geneName] = pvalue
    #病例样本数据剪切并转置
    #print(res)
    dat_T_test = data_cut(dat)
    #正常样本数据剪切并转置
    HC_test = data_cut(tes)
    Y = list(res.keys())
    disease_t = dat_T_test.loc[:, Y]
    HC_test = HC_test.loc[:, Y]
    #print(disease_t)
    return disease_t, HC_test, res
def foldchange(disease_t,HC_test,res):
    r_res = {}
    disease_ave = np.average(disease_t, axis=0)
    HC_ave = np.average(HC_test, axis=0)
    foldchange = disease_ave / HC_ave
    np.average(foldchange,axis=0)
    chi2value = chi2.ppf(0.025,len(res))
    pf = (len (res)*np.average(foldchange))/chi2value
    Y = list(res.keys())
    for i in range(disease_t.shape[1]):
        geneName = Y[i]
        if foldchange[i]>pf:
            r_res[geneName] = foldchange[i]
    return r_res
def merge_data(dat,tes,r_res):
    data = pd.merge(dat, tes)
    df = data.iloc[:, 6:]
    Y = list(r_res.keys())
    df = df.transpose()
    y = data.iloc[:, 2].values
    df.columns = [y]
    df = df.loc[:, Y]
    return df

In [2]:
from sklearn import preprocessing
#读取数据集
dat, tes = data_get()
disease_t, HC_test_1, res = T_test_r()
##T-test
res = T_test(dat,tes)
#病例样本数据剪切并转置
dat_T_test = data_cut(dat)
#正常样本数据剪切并转置
HC_test = data_cut(tes)
#选取T-test检验之后的特征数据
Y = list(res.keys())
disease_t = dat_T_test.loc[:, Y]
HC_test = HC_test.loc[:, Y]
##foldchange
r_res = foldchange(disease_t,HC_test,res)

In [3]:
from sklearn import preprocessing
#读取数据集
dat_ace, tes_ace = data_get()

data_merge = pd.merge(dat_ace, tes_ace)
df_data = data_merge.iloc[:, 6:]

df_data = df_data.transpose()

y = dat.iloc[:, 2].values

df_data.columns = [y]

dis_lab = [1]*dat.iloc[0:,6:].shape[1]
HC_lab = [0]*tes.iloc[0:,6:].shape[1]
df_lab = dis_lab+HC_lab

df_Z = preprocessing.scale(df_data, axis=0, with_mean=True, with_std=True, copy=True)
df_data = pd.DataFrame(df_Z,columns=df_data.columns, index=df_data.index)

In [4]:
from sklearn import preprocessing

In [5]:
disese = pd.read_csv(r"D:\jupyter\new_funtion\smote_and_reduce\新建文件夹\原始\o_reduce.csv")
df_lab_a = disese['Label']
data_a = disese.drop(columns=['Label'])

In [6]:
df_Z = preprocessing.scale(data_a, axis=0, with_mean=True, with_std=True, copy=True)
data_a = pd.DataFrame(df_Z,columns=data_a.columns, index=data_a.index)

In [7]:
data_a

A1BG       A2M     A2ML1   A3GALT2    A4GALT     A4GNT      AAAS  \
0   -0.464738  0.165635 -0.776930 -0.533893 -0.488986  0.472325 -0.460625   
1   -0.529350 -0.362081 -0.106270  0.635730 -0.048459  1.269888 -0.836597   
2    3.376752  2.207034  1.673667  2.283155  1.932276  0.477971  1.447131   
3   -0.401244 -0.521436  0.583021 -1.179622  1.976504  1.416913  1.163961   
4   -0.283191 -0.110779 -0.276101  0.114847 -1.129858  0.478618 -0.329890   
..        ...       ...       ...       ...       ...       ...       ...   
511 -0.693619 -1.092589 -1.729358 -0.789183 -0.466170 -0.283441 -0.409324   
512  0.055669 -0.482278 -1.314463 -0.266589 -0.505999 -0.239683  0.107789   
513  0.447944 -2.157029 -1.733407 -0.632187  0.126728  0.180897 -0.115471   
514  0.442404  0.566518 -0.956442 -0.434927 -0.286979 -0.585276  0.013215   
515  1.080755 -0.141150 -1.145269  0.337271 -0.268564  0.820915 -0.180471   

         AACS     AADAC   AADACL1  ...      ZXDB      ZXDC    ZYG11B  \
0   -0.266150 -0.381410  0.078677  ... -0.379629  1.116348  0.588266   
1    0.465507  1.045813 -1.696345  ...  0.415262  0.734922  0.111870   
2   -2.422171 -1.236056 -2.669829  ... -0.994284 -1.901082 -2.324083   
3   -2.644696  0.236943 -2.272333  ...  0.322406  2.415247 -0.873750   
4    0.686106  0.350797  0.362004  ...  0.065769  0.107750  0.935793   
..        ...       ...       ...  ...       ...       ...       ...   
511  0.860217  0.269650  1.173811  ... -0.309042 -1.288714  0.549111   
512  0.856631  0.145982  0.553338  ...  0.323194 -1.338219 -0.198250   
513  0.262806  0.947090  0.711319  ... -0.682926 -0.089503  0.174419   
514  0.550381  0.450361  0.488089  ... -0.634809 -0.714435 -0.110300   
515  1.399120 -0.554113  0.486968  ... -1.135609 -1.254843 -0.159603   

      ZYG11BL       ZYX     ZZEF1      ZZZ3  tcag7.1017  tcag7.216  tcag7.981  
0   -0.742054 -1.322639  0.673953  0.396322   -0.565415  -0.108897   0.288795  
1    0.445263 -0.963160 -0.586524  0.414752   -0.504560  -1.057707  -0.516178  
2   -0.349661  2.120619 -0.322103 -0.206622   -2.395449   2.046565  -2.390599  
3   -0.256786 -1.106544  0.962924  1.062059   -0.610826  -2.346976  -1.236056  
4    0.511097 -0.110233  0.049429 -0.855981    0.023273   0.363989   1.184409  
..        ...       ...       ...       ...         ...        ...        ...  
511 -0.718844 -0.604180 -0.635116  0.451399    0.529126  -0.989512   1.447955  
512  1.351681  0.907118  0.390142 -0.938794    0.691297   1.319685   0.217344  
513 -0.381640 -0.843938  1.373120  0.457326    0.882043  -1.508854   0.781629  
514  0.255281  0.021853  0.966207 -0.553317    0.988398  -0.866393   0.597504  
515  1.138827  0.430686  0.529887 -1.261444    0.990395  -0.280883   0.932854  

[516 rows x 16828 columns]

In [8]:
from collections import defaultdict

# 用于存储数据的字典
gene_dict = defaultdict(set)

# 打开文件并逐行读取
with open(r'D:\jupyter\new_funtion\download.txt', 'r') as file:
    # 跳过文件的第一行（如果包含列名）
    next(file)

    for line in file:
        # 以制表符分割每行数据
        data = line.strip().split('\t')

        # 检查数据行是否有效
        if len(data) == 8:
            # 提取第二列和第五列数据
            gene1 = data[1]
            gene2 = data[4]

            # 将数据添加到字典中
            gene_dict[gene1].add(gene2)
            gene_dict[gene2].add(gene1)

# 打印结果
for gene, related_genes in gene_dict.items():
    print(f'{gene}: {related_genes}')

S100A4: {'FTH1', 'BNIP3', 'AR'}
BNIP3: {'S100A4', 'RNF227', 'SELENOW', 'AR'}
FOXQ1: {'CLDN3', 'LSM4', 'REPS2', 'KIAA2013', 'AR', 'NRXN3'}
NRXN3: {'DOK6', 'HSD17B2', 'FOXQ1', 'NMU', 'AR'}
HLA-G: {'HLA-B', 'LILRB1', 'LILRB4', 'KIR2DL4', 'HLA-A', 'AR', 'LILRB2'}
LILRB1: {'NFE2L2', 'DUSP18', 'SPRYD4', 'HLA-G', 'AR', 'PLA2G4F', 'PRSS27'}
MTRNR2L1: {'RANBP2', 'ND4', 'RPL27A', 'CDADC1', 'H3F3C', 'MAPK12', 'ZNF285', 'MTRNR2L4', 'UBXN7', 'PATL1', 'LEF1', 'EEF1A1', 'LDHA', 'SLF2', 'OVCH2', 'MTRNR2L3', 'NAA50', 'ANTXR2', 'TANC2', 'RPLP0', 'FAT1', 'MTRNR2L10', 'MTRNR2L6', 'MTRNR2L8', 'TINCR', 'DKC1', 'MTRNR2L5', 'RPS19'}
MTRNR2L8: {'CCDC177', 'SEC61A2', 'DOC2A', 'EIF1AX', 'ND5', 'TLL1', 'ND4', 'NPM1', 'BMPR1B', 'TICRR', 'TAF5', 'ACTN1', 'EEF1A1', 'APH1A', 'RASL12', 'TRIB1', 'TAS2R50', 'PHF20', 'TRIM28', 'EMC10', 'YLPM1', 'OTUD7B', 'KMT2D', 'RALA', 'MTRNR2L9', 'KDM3B', 'MTRNR2L6', 'MRFAP1', 'MTRNR2L10', 'DACT3', 'DPYSL4', 'MTRNR2L1', 'MCOLN3', 'TINCR', 'CD24', 'MTRNR2L7', 'RPL14'}
RAC1: {'SLC44A1',

In [9]:
#第二版代码,矩阵运算方法
from sklearn.metrics import accuracy_score, precision_score
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
import math
import matplotlib.pyplot as plt
from sklearn.metrics import mean_squared_error
from sklearn import datasets
from sklearn.model_selection import train_test_split
from sklearn.linear_model import Lasso
from sklearn.linear_model import LassoCV
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LinearRegression
warnings.filterwarnings("ignore")

from sklearn.preprocessing import StandardScaler


#df_1 = df_data[list(res.keys())]
df_1 = data_a
data_los = data_a
feature_columns = df_1.columns.get_level_values(0).values
df_lab =  df_lab_a

# 用于存储 ACE 值
ace_values = []
mse_values = []
rmse_values = []
alpha = []

ace_output_file = r'D:\jupyter\new_funtion\T_and_F_result\ace_results.txt'
coefs_output_file = r'D:\jupyter\new_funtion\T_and_F_result\model_coefficients.txt'

with open(ace_output_file, 'w') as ace_f, open(coefs_output_file, 'w') as coefs_f:
    total_ace = 0  # 用于累计 ACE 的总和
    for column_name in feature_columns:
        #计算疾病样本ex
        # 选择当前特征作为因变量
        dependent_variable = data_los[column_name]

        # 使用除当前特征外的其他特征作为自变量
        independent_variables = data_los.drop(columns=[column_name])

        related_genes = gene_dict.get(column_name, set())
        
           # 确保只包含存在于 independent_variables 中的基因名
        existing_genes = [gene for gene in related_genes if gene in independent_variables.columns]

    # 计算 ACE
    # 仅当存在至少一个有效基因时才继续
        if existing_genes:

            X = data_los[existing_genes]
            y = data_los[column_name]
            linear_model = LinearRegression()
            linear_model.fit(X, y)
            coefs = linear_model.coef_
            data_esv_1 = independent_variables.loc[:, existing_genes]
            #print(data_esv_1)
            data_esv_1 = data_esv_1 * coefs
            f_s = (data_esv_1 * data_esv_1 * coefs).sum(axis=1)
            esv_1 = data_esv_1.sum(axis=1)
            variance_per_column = independent_variables.loc[:, existing_genes].var()
        else:
            # X_train, X_test, y_train, y_test = train_test_split(independent_variables, dependent_variable, test_size=0.2, random_state=0)
            # 使用 LassoCV 选择最佳 alpha 值
            # alpharange = np.logspace(-10,-2,200,base=10)
            # lasso_alp = LassoCV(alphas=alpharange, cv=5).fit(X_train, y_train)
            best_alpha = 0.01
            lr_lasso = Lasso(alpha=best_alpha).fit(independent_variables, dependent_variable)
            # 获取非零模型系数的行

            non_zero_coefs = lr_lasso.coef_ != 0
            data_esv_1 = independent_variables.loc[:, non_zero_coefs]

            data_esv_1 = data_esv_1 * lr_lasso.coef_[non_zero_coefs]

            f_s = (data_esv_1 * lr_lasso.coef_[non_zero_coefs]).sum(axis=1)
            esv_1 = data_esv_1.sum(axis=1)
            variance_per_column = independent_variables.loc[:, non_zero_coefs].var()
            # 计算 ACE
        data_d = data_los[column_name]

        f = esv_1
        e = (f-f_s)**2
        product_of_variances = variance_per_column.prod()
        e_s = e/(2*product_of_variances)
        pi = math.pi
        sqrt_pi = math.sqrt(2*pi)
        abs_product_of_variances = abs(product_of_variances)

       # 限制 e_s 中的值的大小
        e_s_clipped = e_s.clip(-np.inf, 700)  # 700 是一个示例阈值，可以根据需要调整

        # 计算每个数据点的指数，使用 numpy 的 exp 函数
        e_e_s = e_s_clipped.apply(np.exp)
        # 计算每个数据点的指数
        #e_e_s = e_s.apply(lambda x: math.exp(x))
        # 构造核函数计算
        e_f = (1 / (sqrt_pi * abs_product_of_variances)) * e_e_s

        ax_0 = [1]*data_los.shape[0]

        Logist_data = pd.DataFrame({'a0': ax_0,'f': f, 'f^2': f**2, 'e(f)': e_f, 'e(f)^2': e_f**2, 'f*e(f)': f * e_f}, index=data_los.index)
        #print(Logist_data)
# 处理无限值：将无限值替换为 NaN
        Logist_data = np.where(np.isinf(Logist_data), np.nan, Logist_data)

# 使用与 X_train 相同的方法替换 NaN 和无限值
        median_values = np.nanmedian(Logist_data, axis=0)
        max_values = np.nanmax(Logist_data, axis=0)
        min_values = np.nanmin(Logist_data, axis=0)
        Logist_data = np.nan_to_num(Logist_data, nan=median_values, posinf=max_values, neginf=min_values)
        #print("Logist_data 样本数:", Logist_data)
        #print("y 样本数:", len(df_lab))
        y = df_lab

        X_train, X_test, y_train, y_test = train_test_split(Logist_data, y, test_size=0.2, random_state=0)

        # 创建并训练逻辑回归模型
        # 检查并替换无限值
        #X_train = np.where(np.isinf(X_train), np.nan, X_train)  # 将无限值替换为 NaN
        # 计算中位数、最大值和最小值
        #median_values = np.nanmedian(X_train, axis=0)
        #max_values = np.nanmax(X_train, axis=0)
        #min_values = np.nanmin(X_train, axis=0)

        # 替换 NaN、正无限大和负无限大
        #X_train = np.nan_to_num(X_train, nan=median_values, posinf=max_values, neginf=min_values)
        #X_train = np.nan_to_num(X_train, nan=np.nanmedian(X_train), posinf=np.nanmax(X_train), neginf=np.nanmin(X_train))

        # 对数变换以减小极大值的影响
        #X_train = np.log1p(X_train)

        # 重新训练模型
        model_logi = LogisticRegression()
        model_logi.fit(X_train, y_train)
        y_prob = model_logi.predict_proba(Logist_data)
        # 找到每个样本中概率最大的类别（0或1）和相应的概率值
        max_prob_values = np.max(y_prob, axis=1)

        sum = 0
        for i in range(len(df_lab)):
            sum = abs(df_lab[i] - max_prob_values[i]) + sum
        ace = sum/len(df_lab)    

        # 将 ACE 值、MSE、RMSE、准确度和精确度 添加到列表中
        # 去除特征名称中的括号和逗号
        #cleaned_column_name = column_name[0].replace('(', '').replace(')', '').replace(',', '')
    
        # 将特征名称和 ACE 值添加到列表中
        ace_values.append({"特征": column_name, "ACE": ace})
        
        print('==============================')
        print(f"特征 '{column_name}' 的 ACE: {ace}")
        

# 将 ACE 值列表转换为 DataFrame
ace_df = pd.DataFrame(ace_values)
print(ace_df)
# 保存 ACE 值 DataFrame 为 CSV 文件
ace_csv_file = r'D:\jupyter\new_funtion\Reduce\reduce_o\ace_results.csv'
ace_df.to_csv(ace_csv_file, index=False)
 

特征 'A1BG' 的 ACE: 0.5000554752303997
特征 'A2M' 的 ACE: 0.48068525574904236
特征 'A2ML1' 的 ACE: 0.47904787856940445
特征 'A3GALT2' 的 ACE: 0.49963530189132216
特征 'A4GALT' 的 ACE: 0.4863959325843263
特征 'A4GNT' 的 ACE: 0.4983971182422069
特征 'AAAS' 的 ACE: 0.5210104142768509
特征 'AACS' 的 ACE: 0.5
特征 'AADAC' 的 ACE: 0.49876491021183067
特征 'AADACL1' 的 ACE: 0.4618653679429774
特征 'AADACL2' 的 ACE: 0.4966533084498836
特征 'AADAT' 的 ACE: 0.506703958986874
特征 'AAK1' 的 ACE: 0.474530624292392
特征 'AAMP' 的 ACE: 0.5029343993662265
特征 'AANAT' 的 ACE: 0.4914296481190326
特征 'AARS' 的 ACE: 0.5014850505648377
特征 'AARSD1' 的 ACE: 0.5
特征 'AASDHPPT' 的 ACE: 0.5030822165526253
特征 'AASS' 的 ACE: 0.5015657059876665
特征 'AATF' 的 ACE: 0.48690863303140725
特征 'AATK' 的 ACE: 0.4795495595123272
特征 'ABAT' 的 ACE: 0.4854732275051305
特征 'ABCA1' 的 ACE: 0.5016697529558581
特征 'ABCA10' 的 ACE: 0.4901414268842405
特征 'ABCA11' 的 ACE: 0.490550838602699
特征 'ABCA12' 的 ACE: 0.49371418183679716
特征 'ABCA13' 的 ACE: 0.49945306160842423
特征 'ABCA2' 的 ACE: 0.4711

In [10]:
ace_df_sorted = ace_df.sort_values(by="ACE", ascending=True)
ace_df_sorted
# 将 ACE 值列表转换为 DataFrame
ace_df_sorted_csv = pd.DataFrame(ace_df_sorted)

# 保存 ACE 值 DataFrame 为 CSV 文件
ace_csv_sortd_file = r'D:\jupyter\new_funtion\Reduce\reduce_o\ace_sorted_result.csv'
ace_df_sorted_csv.to_csv(ace_csv_sortd_file, index=False)

In [11]:
ace_values = []
average_ace = []
for column_name in feature_columns:
    dependent_variable = data_los[column_name]
    
    # Use all columns except the current one as independent variables
    independent_variables = data_los.drop(columns=[column_name])
    # 使用除当前特征外的其他特征作为自变量

    related_genes = gene_dict.get(column_name, set())
        
           # 确保只包含存在于 independent_variables 中的基因名
    existing_genes = [gene for gene in related_genes if gene in independent_variables.columns]
    
    matching_rows = ace_df_sorted[ace_df_sorted['特征'].isin(existing_genes)]
    
    # 提取 ACE 值
    ace_values_e = matching_rows['ACE'].values
    ace_values_mean = ace_values_e.mean()

    cleaned_column_name = column_name[0].replace('(', '').replace(')', '').replace(',', '')

    average_ace.append({"特征": column_name, "ACE": ace_values_mean})
    #print(average_ace)

# 将 ACE 值列表转换为 DataFrame
average_ace_df = pd.DataFrame(average_ace)
print(average_ace_df)
# 保存 ACE 值 DataFrame 为 CSV 文件
ace_csv_file = r'D:\jupyter\new_funtion\Reduce\reduce_o\average_ace_results.csv'
average_ace_df.to_csv(ace_csv_file, index=False)

               特征       ACE
0            A1BG  0.488143
1             A2M  0.478076
2           A2ML1  0.491267
3         A3GALT2  0.486132
4          A4GALT  0.486132
...           ...       ...
16823       ZZEF1  0.487320
16824        ZZZ3  0.483621
16825  tcag7.1017       NaN
16826   tcag7.216       NaN
16827   tcag7.981       NaN

[16828 rows x 2 columns]


In [12]:
disese = pd.read_csv(r"D:\jupyter\new_funtion\smote_and_reduce\新建文件夹\原始\o_reduce.csv")
df_lab = disese['Label']
data_a = disese.drop(columns=['Label'])

In [13]:
import pandas as pd
from sklearn.model_selection import cross_val_score, cross_val_predict
from sklearn.naive_bayes import GaussianNB
from xgboost import XGBClassifier
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score, f1_score
import numpy as np

# 读取特征排名文件
csv_file_path = r"D:\jupyter\new_funtion\Reduce\reduce_o\ace_sorted_result.csv"
df = pd.read_csv(csv_file_path)
features = df['特征']
# 获取特征


# 初始化贝叶斯分类器
classifier = SVC()

# 保存所有结果的列表
results = []

data_test = data_a
label = df_lab

# 逐步增加特征并进行交叉验证
for num_features in range(1, 500):
    # 选择当前数量的特征
    selected_features = features[:num_features]
    #print(selected_features)
    # 获取训练数据，假设 X 是你的特征矩阵，y 是你的目标变量
    X = data_test[selected_features]
   
    y = label

    # 进行十折交叉验证
    cross_val_scores = cross_val_score(classifier, X, y, cv=10, scoring='accuracy')
    cross_val_predictions = cross_val_predict(classifier, X, y, cv=10)

    # 计算 F1 分数
    f1 = f1_score(y, cross_val_predictions, average='weighted')

    # 输出结果
    accuracy_mean = np.mean(cross_val_scores)
    print(f"使用 {num_features} 个特征的交叉验证准确度: {accuracy_mean}, F1 分数: {f1}")

    # 将结果添加到列表
    results.append({'NumFeatures': num_features, 'Accuracy': accuracy_mean, 'F1Score': f1})

# 将列表转换为 DataFrame
result_df = pd.DataFrame(results)

# Drop rows with missing F1Score values
result_df_cleaned = result_df.dropna(subset=['F1Score'])

# Find the index of the maximum F1 Score
max_f1_index = result_df_cleaned['F1Score'].idxmax()

# Find the corresponding values
best_num_features = result_df_cleaned.loc[max_f1_index]['NumFeatures']
best_f1_score = result_df_cleaned.loc[max_f1_index]['F1Score']

print(f"最高 F1 Score 对应的特征数量: {best_num_features}, 最高 F1 Score: {best_f1_score}")

# 将所有 F1 Score 保存到文件
#with open(r'D:\jupyter\new_funtion\result\SVC_1_1.txt', 'w') as file:
    #for f1_score in result_df_cleaned['F1Score']:
        #file.write(str(f1_score) + '\n')

# 将结果保存到文件
#result_df_cleaned.to_csv(r'D:\jupyter\new_funtion\result\SVC_1_1.csv', index=False)

使用 1 个特征的交叉验证准确度: 0.746078431372549, F1 分数: 0.7379746099428239
使用 2 个特征的交叉验证准确度: 0.7751131221719457, F1 分数: 0.7709790477356556
使用 3 个特征的交叉验证准确度: 0.7985294117647058, F1 分数: 0.792962962962963
使用 4 个特征的交叉验证准确度: 0.8411764705882352, F1 分数: 0.8381058785717566
使用 5 个特征的交叉验证准确度: 0.8411387631975866, F1 分数: 0.8384421534936999
使用 6 个特征的交叉验证准确度: 0.8586726998491704, F1 分数: 0.8572397718443842
使用 7 个特征的交叉验证准确度: 0.8605203619909501, F1 分数: 0.8593473158173696
使用 8 个特征的交叉验证准确度: 0.8644042232277526, F1 分数: 0.8631569376250228
使用 9 个特征的交叉验证准确度: 0.8605580693815987, F1 分数: 0.8594430992736077
使用 10 个特征的交叉验证准确度: 0.8586349924585217, F1 分数: 0.8575378110261832
使用 11 个特征的交叉验证准确度: 0.8586349924585217, F1 分数: 0.8575378110261832
使用 12 个特征的交叉验证准确度: 0.8605580693815987, F1 分数: 0.8593473158173696
使用 13 个特征的交叉验证准确度: 0.8586349924585217, F1 分数: 0.8576282717565907
使用 14 个特征的交叉验证准确度: 0.8645550527903468, F1 分数: 0.8633474576271188
使用 15 个特征的交叉验证准确度: 0.8547511312217194, F1 分数: 0.8536347373556676
使用 16 个特征的交叉验证准确度: 0.854751131221719

In [14]:
import pandas as pd
from sklearn.model_selection import cross_val_score, cross_val_predict
from sklearn.naive_bayes import GaussianNB
from xgboost import XGBClassifier
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score, f1_score
import numpy as np

# 读取特征排名文件

# 获取特征
features =  df['特征']


# 初始化贝叶斯分类器
classifier = GaussianNB()

# 保存所有结果的列表
results = []


# 逐步增加特征并进行交叉验证
for num_features in range(1, 500):
    # 选择当前数量的特征
    selected_features = features[:num_features]

    # 获取训练数据，假设 X 是你的特征矩阵，y 是你的目标变量
    X = data_test[selected_features]
    y = label

    # 进行十折交叉验证
    cross_val_scores = cross_val_score(classifier, X, y, cv=10, scoring='accuracy')
    cross_val_predictions = cross_val_predict(classifier, X, y, cv=10)

    # 计算 F1 分数
    f1 = f1_score(y, cross_val_predictions, average='weighted')

    # 输出结果
    accuracy_mean = np.mean(cross_val_scores)
    print(f"使用 {num_features} 个特征的交叉验证准确度: {accuracy_mean}, F1 分数: {f1}")

    # 将结果添加到列表
    results.append({'NumFeatures': num_features, 'Accuracy': accuracy_mean, 'F1Score': f1})

# 将列表转换为 DataFrame
result_df = pd.DataFrame(results)

# Drop rows with missing F1Score values
result_df_cleaned = result_df.dropna(subset=['F1Score'])

# Find the index of the maximum F1 Score
max_f1_index = result_df_cleaned['F1Score'].idxmax()

# Find the corresponding values
best_num_features = result_df_cleaned.loc[max_f1_index]['NumFeatures']
best_f1_score = result_df_cleaned.loc[max_f1_index]['F1Score']

print(f"最高 F1 Score 对应的特征数量: {best_num_features}, 最高 F1 Score: {best_f1_score}")

# 将所有 F1 Score 保存到文件
#with open(r'D:\jupyter\new_funtion\result\GaussianNB_1_1.txt', 'w') as file:
    #for f1_score in result_df_cleaned['F1Score']:
        #file.write(str(f1_score) + '\n')

# 将结果保存到文件
#result_df_cleaned.to_csv(r'D:\jupyter\new_funtion\result\GaussianNB_1_1.csv', index=False)

使用 1 个特征的交叉验证准确度: 0.730580693815988, F1 分数: 0.7251185197392375
使用 2 个特征的交叉验证准确度: 0.7693815987933634, F1 分数: 0.7629472920229624
使用 3 个特征的交叉验证准确度: 0.8005656108597284, F1 分数: 0.7958413841053752
使用 4 个特征的交叉验证准确度: 0.8372926093514328, F1 分数: 0.8346658529142508
使用 5 个特征的交叉验证准确度: 0.8449849170437405, F1 分数: 0.8429773443086895
使用 6 个特征的交叉验证准确度: 0.8332956259426847, F1 分数: 0.8312006451318412
使用 7 个特征的交叉验证准确度: 0.8410633484162895, F1 分数: 0.8393255866940078
使用 8 个特征的交叉验证准确度: 0.839102564102564, F1 分数: 0.8376835762066287
使用 9 个特征的交叉验证准确度: 0.843024132730015, F1 分数: 0.8414746543778803
使用 10 个特征的交叉验证准确度: 0.8391402714932127, F1 分数: 0.8375604483131364
使用 11 个特征的交叉验证准确度: 0.8352564102564102, F1 分数: 0.8336462422483928
使用 12 个特征的交叉验证准确度: 0.8333710407239818, F1 分数: 0.8317535904396488
使用 13 个特征的交叉验证准确度: 0.8411010558069382, F1 分数: 0.8394548324429334
使用 14 个特征的交叉验证准确度: 0.8430618401206637, F1 分数: 0.8414746543778803
使用 15 个特征的交叉验证准确度: 0.8430618401206637, F1 分数: 0.8412193092758831
使用 16 个特征的交叉验证准确度: 0.8391402714932127

In [15]:
import pandas as pd
from sklearn.model_selection import cross_val_score, cross_val_predict
from sklearn.naive_bayes import GaussianNB
from xgboost import XGBClassifier
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score, f1_score
import numpy as np

# 读取特征排名文件
# 获取特征
features =  df['特征']


# 初始化贝叶斯分类器
classifier = XGBClassifier()

# 保存所有结果的列表
results = []


# 逐步增加特征并进行交叉验证
for num_features in range(1, 500):
    # 选择当前数量的特征
    selected_features = features[:num_features]

    # 获取训练数据，假设 X 是你的特征矩阵，y 是你的目标变量
    X = data_test[selected_features]
    y = label

    # 进行十折交叉验证
    cross_val_scores = cross_val_score(classifier, X, y, cv=10, scoring='accuracy')
    cross_val_predictions = cross_val_predict(classifier, X, y, cv=10)

    # 计算 F1 分数
    f1 = f1_score(y, cross_val_predictions, average='weighted')

    # 输出结果
    accuracy_mean = np.mean(cross_val_scores)
    print(f"使用 {num_features} 个特征的交叉验证准确度: {accuracy_mean}, F1 分数: {f1}")

    # 将结果添加到列表
    results.append({'NumFeatures': num_features, 'Accuracy': accuracy_mean, 'F1Score': f1})

# 将列表转换为 DataFrame
result_df = pd.DataFrame(results)

# Drop rows with missing F1Score values
result_df_cleaned = result_df.dropna(subset=['F1Score'])

# Find the index of the maximum F1 Score
max_f1_index = result_df_cleaned['F1Score'].idxmax()

# Find the corresponding values
best_num_features = result_df_cleaned.loc[max_f1_index]['NumFeatures']
best_f1_score = result_df_cleaned.loc[max_f1_index]['F1Score']

print(f"最高 F1 Score 对应的特征数量: {best_num_features}, 最高 F1 Score: {best_f1_score}")

# 将所有 F1 Score 保存到文件
#with open(r'D:\jupyter\new_funtion\result\XGBClassifier_1_1.txt', 'w') as file:
    #for f1_score in result_df_cleaned['F1Score']:
        #file.write(str(f1_score) + '\n')

# 将结果保存到文件
#result_df_cleaned.to_csv(r'D:\jupyter\new_funtion\result\XGBClassifier_1_1.csv', index=False)

使用 1 个特征的交叉验证准确度: 0.7478883861236802, F1 分数: 0.7474207395135176
使用 2 个特征的交叉验证准确度: 0.8719079939668175, F1 分数: 0.8718157181571816
使用 3 个特征的交叉验证准确度: 0.8759426847662143, F1 分数: 0.8757000903342368
使用 4 个特征的交叉验证准确度: 0.8933257918552038, F1 分数: 0.8932950328424203
使用 5 个特征的交叉验证准确度: 0.901131221719457, F1 分数: 0.9009988149652955
使用 6 个特征的交叉验证准确度: 0.9009803921568628, F1 分数: 0.9010286015156359
使用 7 个特征的交叉验证准确度: 0.9067873303167421, F1 分数: 0.9068872180451129
使用 8 个特征的交叉验证准确度: 0.914630467571644, F1 分数: 0.9147081805613992
使用 9 个特征的交叉验证准确度: 0.9088612368024134, F1 分数: 0.9088733161741221
使用 10 个特征的交叉验证准确度: 0.9107843137254902, F1 分数: 0.9108192188040097
使用 11 个特征的交叉验证准确度: 0.9030542986425341, F1 分数: 0.903064368265228
使用 12 个特征的交叉验证准确度: 0.8952488687782806, F1 分数: 0.895271743215816
使用 13 个特征的交叉验证准确度: 0.9029411764705882, F1 分数: 0.9030075187969925
使用 14 个特征的交叉验证准确度: 0.9010935143288086, F1 分数: 0.9010553940902443
使用 15 个特征的交叉验证准确度: 0.9068627450980392, F1 分数: 0.9068634086909436
使用 16 个特征的交叉验证准确度: 0.9088612368024134,

In [16]:
# -*- coding: UTF-8 -*-

import numpy as np
import pandas as pd
from collections import Counter
from scipy.stats import pointbiserialr
from math import sqrt
import copy
import math
import warnings
# from pandas.errors import SettingWithCopyWarning
import time
pd.options.mode.chained_assignment = None
# warnings.simplefilter(action="ignore", category=SettingWithCopyWarning)

start_time = time.time()


def loadDataSet(fileName):
    print(f"Loading data from file: {fileName}")
    df = pd.read_csv(fileName)
    return df


def writesortedlist(filename, thelist):
    with open(filename, "w") as fw:
        for item in thelist:
            fw.write(item[0] + "\t" + str(item[1]) + "\n")


def writethelist(filename, thelist):
    with open(filename, "w") as fw:
        for item in thelist:
            fw.write(item + "\n")


def getdatadf(datafile):
    datadf = loadDataSet(datafile)
    labellist = datadf["Label"].tolist()
    del datadf["Label"]
    return datadf, labellist


def CFSmethod(datafile):
    datadf, labellist = getdatadf(datafile)
    print(datadf)
    selectdf = datadf.copy()
    allflist = datadf.columns.tolist()
    namelist = list(datadf.index)
    print(namelist)
    namelist = [int(var) for var in namelist]
    selectdf["class"] = namelist

    bestfset = calBFset(selectdf, allflist)
    writethelist(r"D:\jupyter\new_funtion\data\o_bestfeatureda.txt", bestfset)


def calmulmerit(selectdf, sublist):
    retvalue = 0
    label = "class"
    k = len(sublist)
    namelist = list(selectdf["class"])
    classset = set(namelist)
    caldf = selectdf[sublist]
    allvalue = 0.0
    for feature in sublist:
        caldf = selectdf[sublist]
        middlevalue = 0.0
        for ind in classset:
            caldf[label] = np.where(selectdf[label] == ind, 1, 0)
            coeff = pointbiserialr(caldf[feature], caldf[label])
            middlevalue = abs(coeff.correlation) + middlevalue
        allvalue = middlevalue / float(len(classset)) + allvalue
    allvalue = allvalue / float(k)

    corr = selectdf[sublist].corr()
    corr.values[np.tril_indices_from(corr.values)] = np.nan
    corr = abs(corr)
    rff = corr.unstack().mean()
    retvalue = (k * allvalue) / sqrt(k + k * (k - 1) * rff)
    print(retvalue)
    return retvalue


def calBFset(selectdf, allflist):
    allfdict = getallfscoredict(selectdf, allflist)
    sortedflist = sorted(allfdict.items(), key=lambda item: item[1], reverse=True)
    writesortedlist(r"D:\jupyter\new_funtion\data\o_CFS.txt", sortedflist)
    feaS = []
    feaS.append(sortedflist[0][0])
    maxvalue = sortedflist[0][1]
    for i in range(1, len(sortedflist)):
        print(str(i) + "/" + str(len(sortedflist)))
        itemf = sortedflist[i][0]
        feaS.append(itemf)
        newvalue = calmulmerit(selectdf, feaS)
        if newvalue > maxvalue:
            maxvalue = newvalue
        else:
            feaS.pop()
    print(feaS)
    return feaS


def getallfscoredict(selectdf, allflist):
    retdict = {}
    k = 1
    for f in allflist:
        print(k)
        k = k + 1
        score = calonemerit(selectdf, f)
        if math.isnan(score):
            continue
        retdict[f] = score
    return retdict


def calonemerit(selectdf, subname):
    retvalue = 0
    label = "class"
    namelist = list(selectdf["class"])
    classset = set(namelist)
    caldf = selectdf[subname].to_frame()
    allvalue = 0.0
    for ind in classset:
        caldf[label] = np.where(selectdf[label] == ind, 1, 0)
        coeff = pointbiserialr(caldf[subname], caldf[label])
        allvalue = abs(coeff.correlation) + allvalue
    allvalue = allvalue / float(len(classset))
    return allvalue


datafile = r"D:\jupyter\new_funtion\data\data1\o_adata.csv"
CFSmethod(datafile)
end_time = time.time()

print("时间：", end_time - start_time)


Loading data from file: D:\jupyter\new_funtion\data\data1\o_adata.csv
         A1BG       A2M     A2ML1   A3GALT2    A4GALT     A4GNT      AAAS  \
0   -0.075546 -0.019992 -0.010362  0.015204  0.089450 -0.167457  0.023215   
1    0.021271  0.003967 -0.039111  0.034282 -0.006780  0.068906 -0.004402   
2    0.021271 -0.028230 -0.039111  0.034282 -0.006780  0.068906 -0.004402   
3    0.021789  0.060065 -0.034525 -0.018289  0.094836  0.073653  0.073933   
4    0.027465 -0.021971 -0.068102 -0.014233 -0.232887 -0.281511  0.025672   
..        ...       ...       ...       ...       ...       ...       ...   
692 -0.020314 -0.126988 -0.136339 -0.045191 -0.085769 -0.041509 -0.018460   
693  0.026417 -0.050103 -0.101787 -0.021300 -0.096128 -0.037948  0.038506   
694  0.050881 -0.261083 -0.136676 -0.038014  0.068436 -0.003720  0.013911   
695  0.050536  0.082021 -0.071970 -0.028996 -0.039163 -0.066074  0.028088   
696  0.090348 -0.007129 -0.087696  0.006306 -0.034374  0.048367  0.006751   

     